In [1]:
%pip install web3 cryptowatch-sdk -q
%pip uninstall -y requests -q
%pip install requests -q
%pip install -U kaleido -q
%pip install uniswap-python -q
%pip install protobuf==3.20.0 -q

import os
os.kill(os.getpid(), 9)

ERROR: Could not find a version that satisfies the requirement web3 (from versions: none)
ERROR: No matching distribution found for web3
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
ERROR: Could not find a version that satisfies the requirement requests (from versions: none)
ERROR: No matching distribution found for requests
Note: you may need to restart the kernel to use updated packages.


In [ ]:
%cd /content/drive/MyDrive
!ls

/content/drive/MyDrive
 abi.json
 addrs_0x00bb.json
 addrs_0x0708.json
 addrs_0x1034.json
 addrs_0x1a8C.json
 addrs_0x1Bed.json
 addrs_0x1E89.json
 addrs_0x20f0.json
 addrs_0x27DE.json
 addrs_0x2854.json
 addrs_0x2Faf.json
 addrs_0x36EB.json
 addrs_0x414e.json
 addrs_0x46bF.json
 addrs_0x479D.json
 addrs_0x4bE3.json
 addrs_0x628d.json
 addrs_0x6484.json
 addrs_0x674b.json
 addrs_0x6C73.json
 addrs_0x6F76.json
 addrs_0x7372.json
 addrs_0x7832.json
 addrs_0x86f6.json
 addrs_0x950a.json
 addrs_0x9840.json
 addrs_0x9BBD.json
 addrs_0x9cB2.json
 addrs_0xA23c.json
 addrs_0xaaeE.json
 addrs_0xadE1.json
 addrs_0xb011.json
 addrs_0xb53D.json
 addrs_0xB5B4.json
 addrs_0xBB35.json
 addrs_0xBd57.json
 addrs_0xBDAC.json
 addrs_0xc0a5.json
 addrs_0xC15e.json
 addrs_0xc2ea.json
 addrs_0xc45F.json
 addrs_0xc643.json
 addrs_0xCC0D.json
 addrs_0xd6a3.json
 addrs_0xd8C1.json
 addrs_0xdDc1.json
 addrs_0xE349.json
 addrs_0xe8c6.json
 addrs_0xeb83.json
 addrs_0xed06.json
 addrs_0xf598.json
 addrs_0xfa03.jso

In [ ]:
import requests
import json
import web3
from web3 import Web3
from tqdm import tqdm
import datetime
from sortedcontainers import SortedList
import pickle
import plotly.graph_objects as go
import math
import cryptowatch as cw
import os
from operator import itemgetter
import numpy as np
import time
import logging
from uniswap import Uniswap


ALCHEMY_KEY = "https://eth-mainnet.g.alchemy.com/v2/qFaIQKbLtycYtsMx1qDhY9hYuJ9qGYm_"
ETHERSCAN_API_KEY = "2ZJPPN1PK77474N26RUXHBXTZ4RC19Q4NR"

print('### Configuration')
w3 = Web3(Web3.HTTPProvider(ALCHEMY_KEY))
print('Alchemy connected: ', w3.is_connected())
LATEST_BLOCK = w3.eth.block_number
print('Current block No: ', LATEST_BLOCK)

UNI_ABI = json.load(open('uni_abi.json', 'r'))

factory_address = '0x5C69bEe701ef814a2B6a3EDD4B1652CB9cc5aA6f'
factory_contract = w3.eth.contract(address=factory_address, abi=UNI_ABI)
eth_address = Web3.to_checksum_address("0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2")
eth_decimals = 18


def get_date(timestamp):
  return datetime.datetime.fromtimestamp(timestamp)


def get_pool_in_usd(token_address, blockno=LATEST_BLOCK):
  token_address = Web3.to_checksum_address(token_address)
  pair_address = factory_contract.functions.getPair(token_address, eth_address).call()
  pair_address = Web3.to_checksum_address(pair_address)
  contract = w3.eth.contract(address=pair_address, abi=UNI_ABI)

  try:
    reserves = contract.functions.getReserves().call(block_identifier=blockno)
  except Exception as e:
    logging.info(e)
    logging.info(f'Pool doesnt found: {token_address}')
    return 0, pair_address

  reserve0 = reserves[0]
  reserve1 = reserves[1]

  token0_address = contract.functions.token0().call()
  token1_address = contract.functions.token1().call()

  if token0_address == eth_address:
    pool_eth = reserve0 / (10 ** eth_decimals)
  elif token1_address == eth_address:
    pool_eth = reserve1 / (10 ** eth_decimals)
  return pool_eth, pair_address


def get_native_history(user_address, start_blockno=0, end_blockno=LATEST_BLOCK):
  params = {
      "module": "account",
      "action": "txlist",
      "address": user_address,
      "page": 1,
      "offset": 0,
      "startblock": start_blockno,
      "endblock": end_blockno,
      "sort": "asc",
      "apikey": ETHERSCAN_API_KEY,
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False



def get_erc_history(user_address, start_blockno=0, end_blockno=LATEST_BLOCK):
  params = {
      'module': 'account',
      'action': 'tokentx',
      'address': user_address,
      'page': '1',
      'offset': '0',
      'startblock': start_blockno,
      'endblock': end_blockno,
      'sort': 'asc',
      'apikey': ETHERSCAN_API_KEY
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False

def get_ether_balance_by_block(user_address, blockno=LATEST_BLOCK):
  user_address = Web3.to_checksum_address(user_address)
  return w3.eth.get_balance(user_address, block_identifier=int(blockno)) / (10 ** 18)

def check_if_contract(address):
  checksum = Web3.to_checksum_address(address)
  code = w3.eth.get_code(checksum)
  if code:
    return True
  return False


def get_route_history(route_address, page_number, blockno=LATEST_BLOCK):
  params = {
      'module': 'account',
      'action': 'tokentx',
      'address': route_address,
      'page': page_number,
      'offset': 10000,
      'startblock': '0',
      'endblock': blockno,
      'sort': 'desc',
      'apikey': ETHERSCAN_API_KEY
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False


def get_blockno_by_timestamp(timestamp):
  params = {
      'module': 'block',
      'action': 'getblocknobytime',
      'timestamp': timestamp,
      'closest': 'before',
      'apikey': ETHERSCAN_API_KEY
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False

def get_price(token_address, decimals):
  token_address = Web3.to_checksum_address(token_address)
  try:
    version = 3
    uniswap = Uniswap(address=None, private_key=None, version=version, provider=ALCHEMY_KEY)
    price_out = uniswap.get_price_output(eth, token_address, 10**decimals)
  except:
    try:
      version = 2
      uniswap = Uniswap(address=None, private_key=None, version=version, provider=ALCHEMY_KEY)
      price_out = uniswap.get_price_output(eth, token_address, 10**decimals)
    except:
      price_out = 0
  return price_out / (10 ** decimals_eth)


def nearest_timestamp(input_timestamp, sorted_timestamps):
    idx = sorted_timestamps.bisect_left(input_timestamp)
    if idx == 0:
        return 0
    if idx == len(sorted_timestamps):
        return -1
    before = sorted_timestamps[idx - 1]
    after = sorted_timestamps[idx]
    if after - input_timestamp < input_timestamp - before:
       return idx
    else:
       return idx - 1


def get_token_price(token_symbol, exclude_exchanges=[], ohlc_after=1655446620):
    resp = cw.assets.get(token_symbol)

    token = json.loads(resp._http_response.text)['result']

    exchange_name = ''
    for el in token['markets']['base']:
        if el['exchange'] in exclude_exchanges: continue
        if f'{token_symbol.lower()}usdt' == el['pair'] or f'{token_symbol.lower()}usdc' == el['pair']:
          exchange_name = el['exchange']
          pair = el['pair']
          if 'coinbase' in el['exchange'] or 'binance' in el['exchange'] or 'kraken' in el['exchange'] or 'okx' in el['exchange']:
            break

    if exchange_name:
      resp = cw.markets.get(f"{exchange_name.upper()}:{pair.upper()}",
                            ohlc=True,
                            periods=["1h"],
                            ohlc_after=ohlc_after)
      history = json.loads(resp._http_response.text)['result']
      history = history[list(history.keys())[0]]

      timestamps = [x[0] for x in history]
      open_values = [x[1] for x in history]

      timestamps = SortedList(timestamps)
      closest_ts_idx = nearest_timestamp(1688546207, timestamps)
      diff_seconds = abs(timestamps[closest_ts_idx] - 1688546207)
      three_days_seconds = 3 * 24 * 60 * 60
      if diff_seconds > three_days_seconds:
          token_history = get_token_price(token_symbol, exclude_exchanges+[exchange_name], ohlc_after=ohlc_after)
      else:
        token_history = {'timestamps': timestamps, 'values': open_values }
    else:
        logging.info("Coinbase hasn't found")
        logging.info('\n')
        return {}
    return token_history


def get_token_balance_by_block(user_address, token_address, blockno=LATEST_BLOCK):
  user_address = Web3.to_checksum_address(user_address)
  token_address = Web3.to_checksum_address(token_address)

  if os.path.exists('src/abi.json'):
    token_abi = json.load(open('src/abi.json', 'r'))
  else:
    token_abi = json.load(open('abi.json', 'r'))
  token = w3.eth.contract(address=token_address, abi=token_abi) # declaring the token contract
  try:
    token_balance = token.functions.balanceOf(user_address).call(block_identifier=blockno) # returns int with balance, without decimals
  except web3.exceptions.ABIFunctionNotFound as e:
    logging.info('Error {e}')
  return token_balance

def get_token_info(contract_address):
  params = {
      'module': 'token',
      'action': 'tokeninfo',
      'contractaddress': contract_address,
      'apikey': ETHERSCAN_API_KEY
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False


def get_token_holders(contract_address):
  params = {
      'module': 'token',
      'action': 'tokenholderlist',
      'contractaddress': contract_address,
      'page': '1',
      'offset': '0',
      'apikey': ETHERSCAN_API_KEY
  }

  response = requests.get("https://api.etherscan.io/api", params=params)

  if response.status_code == 200:
      json_response = response.json()
      return json_response['result']

  logging.info(f"Request failed with status code {response.status_code}")
  logging.info(response.text)
  logging.info('\n')
  return False

def get_sell_price(token_address, token_decimals, token_amount):
  token_amount = int(token_amount * 10 ** token_decimals)
  token_address = Web3.to_checksum_address(token_address)
  try:
    version = 2
    uniswap = Uniswap(address=None, private_key=None, version=version, provider=ALCHEMY_KEY)
    price_out = uniswap.get_price_input(token_address, eth_address, token_amount)
    return price_out / (10 ** eth_decimals)
  except Exception as e:
    try:
      version = 3
      uniswap = Uniswap(address=None, private_key=None, version=version, provider=ALCHEMY_KEY)

      price_out = uniswap.get_price_input(token_address, eth_address, token_amount)
      return price_out / (10 ** eth_decimals)
    except Exception as e:
      return None


def main(user_address, ts_after, UNTIL_BLOCKNO, logger, TOKEN_HOLDERS_TRESHOLD, MARKET_CAP_TRESHOLD):
  handler = logging.FileHandler(os.path.join('log.txt'), 'w')
  handler.setFormatter(logging.Formatter('%(message)s'))
  logger.addHandler(handler)

  logging.info(f'Start date {get_date(ts_after)}')
  start_blockno = get_blockno_by_timestamp(ts_after)
  all_txs = get_erc_history(user_address, start_blockno=start_blockno, end_blockno=UNTIL_BLOCKNO)

  unique_addresses = set([tx['contractAddress'] for tx in all_txs])

  lowest_blocks = {}

  for data in tqdm(all_txs, 'Extracting blocks'):
      addr, block = data['contractAddress'], int(data['blockNumber'])
      lowest_blocks[addr] = min(block, lowest_blocks.get(addr, float('inf')))


  print('Unique tokens ', len(unique_addresses))
  # is_scam = {}
  # token_address_to_info = {}
  # for addr in tqdm(unique_addresses, 'Checking for scam'):
  #   pass
    # pool_in_eth = get_pool_in_usd(addr, lowest_blocks[addr])
    # token_address_to_info[addr] = {}
    # token_address_to_info[addr]['pool_in_eth'] = pool_in_eth
    # info = get_token_info(addr)
    # if info:
    #   info = info[0]

    # token_price = float(info['tokenPriceUSD'])
    # total_supply = int(info['totalSupply'])
    # divisor = int(info['divisor'])

    # market_cap = token_price * (total_supply / (10 ** divisor))
    # if TOKEN_HOLDERS_TRESHOLD:
    #   is_scam[addr] = True
    #   continue

    # holders = get_token_holders(addr)
    # is_scam[addr] = len(holders) < TOKEN_HOLDERS_TRESHOLD
    # is_scam[addr] = False
    # print(f"Token {addr}:\nHolders {len(holders)}\nPrice in USD {token_price}, Marketcap {market_cap}")

  for item in all_txs:
      item['timeStamp'] = int(item['timeStamp'])
  all_txs = sorted(all_txs, key=itemgetter('timeStamp'))

  ether_balance = 0
  prev_ether_balance = 0
  tx_hashes = []
  d_all = {}
  symbol2address = {}
  tokens = {}
  for i, tx in enumerate(tqdm(all_txs, "Processing txs")):
    token_symbol = tx['tokenSymbol']
    if not token_symbol in symbol2address:
      symbol2address[token_symbol] = [tx['contractAddress'], int(tx['tokenDecimal'])]

    block_number = int(tx['blockNumber'])

    if tx['hash'] not in tx_hashes:
      tokens = {}
      tx_hashes.append(tx['hash'])
      prev_ether_balance = get_ether_balance_by_block(user_address, block_number-1)
      ether_balance = get_ether_balance_by_block(user_address, block_number)
      gas = (int(tx['gasPrice']) * int(tx['gasUsed']) / 10**18)
      diff_ether = ether_balance - prev_ether_balance

    if 'tokenName' in tx:
      tokens[token_symbol] = float(tx['value']) / (10 ** int(tx['tokenDecimal']))

    if ((i+1) == len(all_txs)) or tx['hash'] != all_txs[i+1]['hash']:
      if diff_ether == 0 or diff_ether + gas == 0 or abs(diff_ether) < 0.03 or abs(diff_ether+gas) < 0.03 :
        continue
      else:
        if len(tokens) == 0:
          continue
        elif len(tokens) > 1:
          continue

      if token_symbol not in d_all:
        d_all[token_symbol] = {}

      token_symbol = list(tokens.keys())[0]
      value = list(tokens.values())[0]

      if tx['from'] == user_address:
        if (diff_ether + gas) < 0:
          print(token_symbol, value, diff_ether, gas, tokens)
          print('Unexpected behaviour')
          print(tx['hash'])
          continue

        if 'amount' not in d_all[token_symbol]:
          continue

        if value > d_all[token_symbol]['amount']:
          diff_ether = (diff_ether / value) * d_all[token_symbol]['amount']
          d_all[token_symbol]['amount'] -= d_all[token_symbol]['amount']
        else:
          d_all[token_symbol]['amount'] -= value

        if 'sold' in d_all[token_symbol]:
          d_all[token_symbol]['sold'] += diff_ether
        else:
          d_all[token_symbol]['sold'] = diff_ether

      else:
        if (diff_ether - gas) > 0:
          print(token_symbol, value, diff_ether, gas, tokens)
          print('Unexpected behaviour')
          print(tx['hash'])
          continue

        if 'bought' in d_all[token_symbol]:
          d_all[token_symbol]['bought'] += abs(diff_ether)
        else:
          d_all[token_symbol]['bought'] = abs(diff_ether)

        if 'amount' not in d_all[token_symbol]:
          d_all[token_symbol]['amount'] = 0
        d_all[token_symbol]['amount'] += value

  print(d_all)
  # exit(0)
  win_rate = 0
  overall = 0
  pnl_released = 0
  pnl_unreleased = 0

  for key, value in tqdm(d_all.items(), 'Count stats'):
    overall += 1
    tokenB, tokenB_decimals = symbol2address[key]
    first_block = lowest_blocks[tokenB]
    pool_in_ether = get_pool_in_usd(tokenB, blockno=first_block)
    pool_in_ether_now = get_pool_in_usd(tokenB, blockno=LATEST_BLOCK)
    d_all[key]['pool_liq_now'] = pool_in_ether_now
    d_all[key]['pool_liq'] = pool_in_ether
    d_all[key]['first_block'] = first_block
    d_all[key]['addr'] = tokenB
    # price = get_price(tokenB,tokenB_decimals)
    # print(key, price)
    if 'bought' in value and 'sold' in value:
      pnl = value['sold'] - value['bought']
      pnl_released += pnl

      d_all[key]['pnl'] = pnl
      d_all[key]['x_amount'] = pnl / value['bought']

      if pnl > 0:
        win_rate += 1
    elif 'bought' in value and 'sold' not in value:
      cur_price = get_sell_price(tokenB, tokenB_decimals, value['bought'])
      if not cur_price:
        continue
      d_all[key]['unpnl'] = cur_price - value['bought']
      pnl_unreleased += d_all[key]['unpnl']
      if d_all[key]['unpnl'] > 0:
        win_rate += 1

  result = {
    'user_address': user_address,
    'tokens': d_all,
    'win_rate': win_rate / max(overall, 1),
    'tokens_amount': overall,
    'win_rate_amount': win_rate,
    'pnl_released': pnl_released,
    'pnl_unreleased': pnl_unreleased,
    'overall_txs': len(set([x['hash'] for x in all_txs]))
  }

  from pprint import pprint
  print('For ', user_address)
  # print('All tokens')
  # pprint(result['tokens'])

  # print('Scam percentage: ', result['scam_percentage'])
  # print(f'Percentage of good token trades: {result["win_rate"]} ({result["win_rate_amount"]}/{result["tokens_amount"]})')
  print('Released profit: ', result['pnl_released'])
  # print('Unreleased profit: ', result['pnl_unreleased'])
  # pprint(result)
  return result


if __name__ == '__main__':
  universal_page_number = 1
  logger = logging.getLogger()
  logger.setLevel(logging.INFO)

  now = int(time.time())
  UNTIL_BLOCKNO = get_blockno_by_timestamp(now)
  ROUTE_ADDRESS = "0x81a460ea6fD96a73D5672F1f4aA684697D4B44Cc"

  addrs = set()
  page_number = 1
  route_erc = get_route_history(ROUTE_ADDRESS, page_number)
  ACTIVITY_PERIOD = now - 2 * 24 * 60 * 60 # 2 days from now
  activity_ts = get_blockno_by_timestamp(ACTIVITY_PERIOD)

  for i, tx in enumerate(tqdm(route_erc, f'Parse addresses from {page_number}')):
    if int(tx['timeStamp']) < int(activity_ts):
      break

    to_contract = check_if_contract(tx['to'])
    if not to_contract:
      addrs.add(tx['to'])
      continue

    from_contract = check_if_contract(tx['from'])
    if not from_contract:
      addrs.add(tx['from'])

    json.dump(list(addrs), open(f'addrs_{ROUTE_ADDRESS[:6]}.json', 'w'))

  addrs = list(addrs)[::-1]
  # addrs = ['0xdfd050f52090ccee9734bbdd45e7a76eebe7be6a']
  # addrs = json.load(open('addrs.json', 'r'))[::-1]

  ts_after = now - 7 * 24 * 60 * 60 * 1  # 1 month from now
  TOKEN_HOLDERS_TRESHOLD = 0
  MARKET_CAP_TRESHOLD = 0 # better set to 0 for now

  # if os.path.exists('output.json'):
  #   output = json.load(open('output.json', 'r'))
  # else:
  output = []
  for addr in tqdm(addrs, 'Address processing'):
    try:
        result = main(addr.lower(), ts_after, UNTIL_BLOCKNO, logger, TOKEN_HOLDERS_TRESHOLD, MARKET_CAP_TRESHOLD)
        output.append(result)

        # if process_route:
        with open(f'output_{ROUTE_ADDRESS[:6]}.json', 'w') as f:
            json.dump(output, f)
    except:
        continue

### Configuration
Alchemy connected:  True
Current block No:  17987270


Address processing:   0%|          | 0/2077 [00:00<?, ?it/s]INFO:root:Start date 2023-08-17 21:34:45

Extracting blocks: 100%|██████████| 5/5 [00:00<00:00, 28225.46it/s]


Unique tokens  3



Processing txs: 100%|██████████| 5/5 [00:00<00:00,  8.24it/s]


{'GUMP': {'bought': 0.14988415515988146, 'amount': 254503.1139506509}, 'DRUGS': {'bought': 0.08006505411440792, 'amount': 2163304.11566776}, 'SHIA': {'bought': 0.3496306647608304, 'amount': 0.0, 'sold': 0.3358627018771156}}


...

Unique tokens  56



Processing txs: 100%|██████████| 245/245 [00:27<00:00,  9.03it/s]


{'SAINT': {'bought': 1.1335459576201465, 'amount': 25.079999999999927, 'sold': 0.7701719950881888}, 'HOUSE': {'bought': 1.37105301306006, 'amount': 25.079999999999927, 'sold': 0.8129538934153734}, 'PSYOP': {'bought': 1.3642103818826117, 'amount': 0.0, 'sold': 0.8752826599179928}, 'Grave': {'bought': 0.17811540382412816, 'amount': 0.0, 'sold': 0.22982295610287068}, 'CROPS': {}, 'DARK': {'bought': 1.3353879365607648, 'amount': 4009.0}, 'BxB': {'bought': 1.8552567979830425, 'amount': 5025.5, 'sold': 1.0522620336465662}, '$PEPE': {'bought': 0.2047005006787278, 'amount': 3009600.0, 'sold': 0.1054640335656194}, 'PIPS': {'bought': 0.15939528320940008, 'amount': 665.0}, 'PNDC': {'bought': 0.6033397264460045, 'amount': 0.0, 'sold': 0.6219126293979016}, 'MONERO': {}, 'BRG': {'bought': 0.711569227476675, 'amount': 70379.09999999963, 'sold': 0.48077930086338566}, 'AER': {'bought': 0.9532385444363383, 'amount': 251275.0, 'sold': 0.8769266154928947}, '0x1': {}, 'SNORKZ': {'bought': 1.653639789611415

Streaming output truncated to the last 5000 lines.
    yielded = ctx_run(next, result)
  File "/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py", line 302, in do_execute
    res = shell.run_cell(code, store_history=store_history, silent=silent)
  File "/usr/local/lib/python3.10/dist-packages/ipykernel/zmqshell.py", line 539, in run_cell
    return super(ZMQInteractiveShell, self).run_cell(*args, **kwargs)
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2975, in run_cell
    result = self._run_cell(
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3030, in _run_cell
    return runner(coro)
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/async_helpers.py", line 78, in _pseudo_sync_runner
    coro.send(None)
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3257, in run_cell_async
    has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


For  0xca317ef5f8978c36c1065184fde08d9dd7c36cfe
Released profit:  -4.78932200606272


hkjhkjhkjgkjhkhjgljkjhkjhmnbmnbmhkkjhkjhkjhjk